In [12]:
#Libraries Installation

!pip install openai
!pip install sentence-transformers

#Importing the dataset
import pandas as pd
import numpy as np

import nltk
nltk.download('punkt')
from nltk import tokenize


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [13]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [14]:
# Read the Excel file into a DataFrame
Translation_df = pd.read_excel('SauLTC_file_Health.xlsx')

en_text = Translation_df['English'].tolist()
ar_text = Translation_df['Arabic'].tolist()

In [15]:
Translation_df

Unnamed: 0                                            English  \
0            0  step 1 inform yourself If you or a loved one h...   
1            1  Try yoga or Pilates. Both these disciplines ar...   
2            2  Introduction: Metabolism is a word frequently ...   
3            3  A GOLDEN AGE FOR THE BRAIN What do we really k...   
4            4  YOUR BRAIN, YOUR WORLD as you move through thi...   
..         ...                                                ...   
80          80  The Two-Week Wait Here’s the thing about tryin...   
81          81  CHAPTER 8 Wisdom from the Circle ONE weekend e...   
82          82  The Synapse Every neuron has a soma, or a cent...   
83          83  Step 3: Eat Bananas Eat 4,700 mg of Potassium ...   
84          84  Introduction In the autumn of 2009 my husband,...   

                                               Arabic  
0   الخطوة الأولى ثقف نفسك اذا تم تشخيصك أو تشخيص ...  
1   حاول ممارسة اليوغا أو بيلاتيس . فأن جميعها مفي...  
2   المقدمة: الأيض هي كلمة كثيرًا ما تستخدم , وناد...  
3   العصر الذهبي للدماغ ما الذي نعرفه حقا عن الدما...  
4   عقلك هو عالمك خلال تصفحك لهذا الكتاب، سترى أن ...  
..                                                ...  
80  إسبوعي الإنتظار تقضين النصف الأول من الشهر بتح...  
81  الفصل الثامن حكم من المحيطين بنا عادة مااجلس ف...  
82  التشابك العصبي: تحتوي كل الخلايا العصبية على ج...  
83  الخطوة الثالثة : تناول الموز تناول البوتاسيوم ...  
84  المقدمة قررتُ أنا وزوجي جيسي في خريف عام 2009 ...  

[85 rows x 3 columns]

In [16]:
from sentence_transformers import SentenceTransformer, util
import numpy as np



# Assuming model is already initialized outside the function
model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-mpnet-base-v2')

def create_segments(doc_id, english_text, arabic_text, segment_word_limit):
    english_sentences = list(tokenize.sent_tokenize(english_text))
    arabic_sentences = list(tokenize.sent_tokenize(arabic_text))

    rows_list = []  # To store the segment pairs
    eng_segment_end = 0  # Tracks the end of the current English segment
    arab_segment_end = 0  # Tracks the end of the matching Arabic segment

    while eng_segment_end < len(english_sentences) and arab_segment_end < len(arabic_sentences):
        current_word_count = 0
        eng_segment = []
        while current_word_count < segment_word_limit and eng_segment_end < len(english_sentences):
            eng_segment.append(english_sentences[eng_segment_end])
            current_word_count += len(english_sentences[eng_segment_end].split())
            eng_segment_end += 1

        # Find the end of the corresponding Arabic segment
        last_eng_sentence = eng_segment[-1]
        last_eng_sentence_embedding = model.encode([last_eng_sentence], convert_to_tensor=True)
        arabic_embeddings = model.encode(arabic_sentences[arab_segment_end:], convert_to_tensor=True)
        similarities = util.pytorch_cos_sim(last_eng_sentence_embedding, arabic_embeddings)
        highest_score_index = np.argmax(similarities.cpu().numpy(), axis=1).item()

        # Determine the Arabic segment
        arabic_segment = arabic_sentences[arab_segment_end:arab_segment_end+highest_score_index+1]
        arab_segment_end += highest_score_index + 1  # Prepare for the next iteration

        # Append the segments to rows_list
        rows_list.append({
            'English Segment': ' '.join(eng_segment),
            'Arabic Segment': ' '.join(arabic_segment),
            'Document_ID': doc_id
        })

    # Create a DataFrame from the list of rows
    df = pd.DataFrame(rows_list)
    return df

# Example of how to use the function (assuming en_text and ar_text are lists of English and Arabic texts)
segments_df = pd.DataFrame(columns=['English Segment', 'Arabic Segment', 'Document_ID'])

for i in range(len(en_text)):  # Assuming en_text and ar_text are defined somewhere
    print(f"Processing document {i}")
    mydf = create_segments(i, en_text[i], ar_text[i], 1000)
    segments_df = pd.concat([segments_df, mydf], ignore_index=True)

segments_df.to_excel("SauLTC_file_Health_Create_Segments.xlsx", index=False)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Processing document 0
Processing document 1
Processing document 2
Processing document 3
Processing document 4
Processing document 5
Processing document 6
Processing document 7
Processing document 8
Processing document 9
Processing document 10
Processing document 11
Processing document 12
Processing document 13
Processing document 14
Processing document 15
Processing document 16
Processing document 17
Processing document 18
Processing document 19
Processing document 20
Processing document 21
Processing document 22
Processing document 23
Processing document 24
Processing document 25
Processing document 26
Processing document 27
Processing document 28
Processing document 29
Processing document 30
Processing document 31
Processing document 32
Processing document 33
Processing document 34
Processing document 35
Processing document 36
Processing document 37
Processing document 38
Processing document 39
Processing document 40
Processing document 41
Processing document 42
Processing document 4

In [17]:
segments_df

English Segment  \
0    step 1 inform yourself If you or a loved one h...   
1    In fact, Hippocrates first described and named...   
2    how cancer develops ‘Solid’ tumours that devel...   
3    Embryonic stem cells, the cells found in the v...   
4    A powerful example of the impact of gene expre...   
..                                                 ...   
464  But this was for the whole city – not just for...   
465  But it doesn’t leave much time for decision th...   
466  Jesse is not. Occasionally, when he thinks I’m...   
467  Please skip ahead. But for a lot of us, we’re ...   
468  When we did start thinking more seriously abou...   

                                        Arabic Segment Document_ID  
0    الخطوة الأولى ثقف نفسك اذا تم تشخيصك أو تشخيص ...           0  
1    فأبقراط في الواقع هو أول من وصفه وأسماه في الي...           0  
2    كيف ينشأ السرطان تمر الأورام الصلبة التي تظهر ...           0  
3    الخلايا الجذعية الجنينية ــ هي الخلايا التي تت...           0  
4    ويعد اليُسْرُوع والفراشة من الأمثلة القوية على...           0  
..                                                 ...         ...  
464  فكلُ ما كانَ علينا فعلُه ، أخذُ السعرِ القديم ...          84  
465  فأُخبرتُ فورًا بأنهُ بإمكاني شرب كوبين من القه...          84  
466  وعندما يتوقع جيسي أحيانًا أنني لا أبحث عنه ، أ...          84  
467  ولكن نحن غالبًا ما نفكر بالحمل قبل أن نحمل بوق...          84  
468  وعندما أفكر جديا بإنجاب طفل ، فإن تفكيري يتمحو...          84  

[469 rows x 3 columns]